# Capstone Project - The Battle of Neighborhoods

## Environment Setup

In [1]:
# Setup
import folium
from folium.plugins import MarkerCluster
from geopy.geocoders import Nominatim
import json
import matplotlib.cm as cm
import matplotlib.colors as colors
import numpy as np
import pandas as pd
import requests
from sklearn.cluster import KMeans

## Web Scraping

In [2]:
url_mrt = 'https://en.wikipedia.org/wiki/List_of_Singapore_MRT_stations'
df = pd.read_html(url_mrt, header = 1, index_col = None)[1]
display(df.head())

In operation                  Future         English • Malay  \
0  North South Line (NSL)  North South Line (NSL)  North South Line (NSL)   
1                NS1 EW24                     JE5             Jurong East   
2                     NS2                     NaN             Bukit Batok   
3                     NS3                     NaN            Bukit Gombak   
4                     NaN                    NS3A               Brickland   

                  Chinese                   Tamil                 Opening  \
0  North South Line (NSL)  North South Line (NSL)  North South Line (NSL)   
1                     裕廊东          ஜூரோங் கிழக்கு           10 March 1990   
2                    武吉巴督       புக்கிட் பாத்தோக்           10 March 1990   
3                    武吉甘柏       புக்கிட் கோம்பாக்           10 March 1990   
4                      红砖            பிரிக்லேன்ட்               Mid-2030s   

  Name(s) during planning stages            Abbreviation  \
0         North South Line (NSL)  North South Line (NSL)   
1                    Jurong East                     JUR   
2              Bukit Batok South                     BBT   
3              Bukit Batok North                     BGB   
4                      Brickland                     TBA   

                    Location(s)       Connection(s) to other transport  
0        North South Line (NSL)                 North South Line (NSL)  
1                   Jurong East  Jurong East Temporary Bus Interchange  
2                   Bukit Batok            Bukit Batok Bus Interchange  
3                   Bukit Batok                                    NaN  
4  Exact location not yet known                                    NaN

In [3]:
# Drop unnecessary columns
keep_columns = ['In operation', 'English • Malay', 'Opening']
df = df[keep_columns]
# Rename columns for easier indexing and readibility
df.columns = ['StationCode', 'StationName', 'Opening']
# Drop rows for stations with NaN StationCode
df.dropna(inplace = True)

display(df.head())

StationCode             StationName                 Opening
0  North South Line (NSL)  North South Line (NSL)  North South Line (NSL)
1                NS1 EW24             Jurong East           10 March 1990
2                     NS2             Bukit Batok           10 March 1990
3                     NS3            Bukit Gombak           10 March 1990
5                 NS4 BP1           Choa Chu Kang           10 March 1990

In [4]:
# Drop rows where StationCode contains words like 'Line', 'Stage', 'Extension', 'Infill'
# These are subheaders in the Wikipedia table
df = df[~df.StationCode.str.contains('|'.join(['Line', 'Stage', 'Extension', 'Infill']))]
display(df.head())

StationCode    StationName           Opening
1    NS1 EW24    Jurong East     10 March 1990
2         NS2    Bukit Batok     10 March 1990
3         NS3   Bukit Gombak     10 March 1990
5     NS4 BP1  Choa Chu Kang     10 March 1990
6         NS5        Yew Tee  10 February 1996

In [5]:
# Drop stations that have not opened in 2020
# First, we extract all the numerical digits from the 'Opening' column, and convert to numeric
df['Opening'] = df.Opening.str.extract('(\d{4})').apply(pd.to_numeric)
# Drop stations that have opening years > 2020
df = df[df['Opening'] <= 2020]

display(df.head())

StationCode    StationName  Opening
1    NS1 EW24    Jurong East     1990
2         NS2    Bukit Batok     1990
3         NS3   Bukit Gombak     1990
5     NS4 BP1  Choa Chu Kang     1990
6         NS5        Yew Tee     1996

In [6]:
# Some station names contain both English and Malay names, e.g. 'Botanic Gardens • Kebun Bunga'
# We will only keep the english names which come before the '•' character
temp = df.StationName.str.split(' • ')
temp = [x[0] for x in temp]
df['StationName'] = temp

In [7]:
# Some stations are interchanges for multiple lines, hence we will drop entries
# with duplicate station names
df.drop_duplicates('StationName', inplace = True)
df.reset_index(drop = True, inplace = True)

In [8]:
#with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#    display(df)
display(df.head())

StationCode    StationName  Opening
0    NS1 EW24    Jurong East     1990
1         NS2    Bukit Batok     1990
2         NS3   Bukit Gombak     1990
3     NS4 BP1  Choa Chu Kang     1990
4         NS5        Yew Tee     1996

## Extracting Latitude and Longitude Data

In [9]:
# Geolocator settings
geolocator = Nominatim(user_agent = 'ny_explorer')

# Extract and add geodata into dataframe
for i in df.index:
    geodata = geolocator.geocode('{} Station, Singapore'.format(df.iloc[i]['StationName']))
    df.at[i, 'Latitude'] = geodata.latitude
    df.at[i, 'Longitude'] = geodata.longitude

display(df.head())

StationCode    StationName  Opening  Latitude   Longitude
0    NS1 EW24    Jurong East     1990  1.332155  103.742984
1         NS2    Bukit Batok     1990  1.349057  103.749591
2         NS3   Bukit Gombak     1990  1.358812  103.751501
3     NS4 BP1  Choa Chu Kang     1990  1.384298  103.743855
4         NS5        Yew Tee     1996  1.397149  103.747527

## Extracting Foursquare Data

### Foursquare API setup

In [10]:
# client_id.txt contains your Foursquare ID
# client_secret.txt contains your Foursquare Secret
with open('client_id.txt', 'r') as f1:
    CLIENT_ID = f1.read()
with open('client_secret.txt', 'r') as f2:
    CLIENT_SECRET = f2.read()
VERSION = '20180605'
LIMIT = 100
RADIUS = 500 # 500m radius

### Function for extracting eateries around location

In [11]:
def getNearbyVenues(names, latitudes, longitudes, radius, limit, section = 'food'):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):

        print(name)    
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&section={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limit,
            section)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Station Name', 
                  'Station Latitude', 
                  'Station Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Extract recommendations from Foursquare

In [12]:
df_food = getNearbyVenues(names = df['StationName'],
                          latitudes = df['Latitude'],
                          longitudes = df['Longitude'],
                          radius = RADIUS,
                          limit = LIMIT,
                          section = 'food')

Jurong East
Bukit Batok
Bukit Gombak
Choa Chu Kang
Yew Tee
Kranji
Marsiling
Woodlands
Admiralty
Sembawang
Canberra
Yishun
Khatib
Yio Chu Kang
Ang Mo Kio
Bishan
Braddell
Toa Payoh
Novena
Newton
Orchard
Somerset
Dhoby Ghaut
City Hall
Raffles Place
Marina Bay
Marina South Pier
Pasir Ris
Tampines
Simei
Tanah Merah
Bedok
Kembangan
Eunos
Paya Lebar
Aljunied
Kallang
Lavender
Bugis
Tanjong Pagar
Outram Park
Tiong Bahru
Redhill
Queenstown
Commonwealth
Buona Vista
Dover
Clementi
Chinese Garden
Lakeside
Boon Lay
Pioneer
Joo Koon
Gul Circle
Tuas Crescent
Tuas West Road
Tuas Link
Expo
Changi Airport
HarbourFront
Chinatown
Clarke Quay
Little India
Farrer Park
Boon Keng
Potong Pasir
Woodleigh
Serangoon
Kovan
Hougang
Buangkok
Sengkang
Punggol
Bras Basah
Esplanade
Promenade
Nicoll Highway
Stadium
Mountbatten
Dakota
MacPherson
Tai Seng
Bartley
Lorong Chuan
Marymount
Caldecott
Botanic Gardens
Farrer Road
Holland Village
one-north
Kent Ridge
Haw Par Villa
Pasir Panjang
Labrador Park
Telok Blangah
Bayfront

Check number of venues returned for each MRT station.

In [13]:
df_food.head()

Station Name  Station Latitude  Station Longitude  \
0  Jurong East          1.332155         103.742984   
1  Jurong East          1.332155         103.742984   
2  Jurong East          1.332155         103.742984   
3  Jurong East          1.332155         103.742984   
4  Jurong East          1.332155         103.742984   

                                               Venue  Venue Latitude  \
0                          Song Fa Bak Kut Teh 松發肉骨茶        1.333394   
1                                        Johan Paris        1.334083   
2  Tonkatsu by Ma Maison とんかつ マメゾン (Tonkatsu by M...        1.333668   
3                    Dian Xiao Er 店小二 (Dian Xiao Er)        1.333447   
4                                          Green Dot        1.333641   

   Venue Longitude                 Venue Category  
0       103.743420             Chinese Restaurant  
1       103.742384                         Bakery  
2       103.742818            Japanese Restaurant  
3       103.743094             Chinese Restaurant  
4       103.742858  Vegetarian / Vegan Restaurant

In [14]:
df_food.groupby('Station Name').count().head()

Station Latitude  Station Longitude  Venue  Venue Latitude  \
Station Name                                                               
Admiralty                    9                  9      9               9   
Aljunied                    38                 38     38              38   
Ang Mo Kio                  39                 39     39              39   
Bartley                      8                  8      8               8   
Bayfront                    34                 34     34              34   

              Venue Longitude  Venue Category  
Station Name                                   
Admiralty                   9               9  
Aljunied                   38              38  
Ang Mo Kio                 39              39  
Bartley                     8               8  
Bayfront                   34              34

List of unique food eateries categories in the dataframe.

In [15]:
print('{} F&B categories.'.format(len(df_food['Venue Category'].unique())))
venuetype_list = df_food['Venue Category'].unique()
print(venuetype_list)

106 F&B categories.
['Chinese Restaurant' 'Bakery' 'Japanese Restaurant'
 'Vegetarian / Vegan Restaurant' 'Indian Restaurant' 'Burger Joint'
 'Seafood Restaurant' 'Korean Restaurant' 'German Restaurant'
 'Hotpot Restaurant' 'Italian Restaurant' 'Ramen Restaurant' 'Salad Place'
 'Café' 'Dumpling Restaurant' 'Sushi Restaurant' 'Halal Restaurant'
 'Asian Restaurant' 'Food Court' 'Cafeteria' 'Sandwich Place'
 'Fast Food Restaurant' 'Steakhouse' 'Dim Sum Restaurant' 'Soup Place'
 'Diner' 'Japanese Curry Restaurant' 'Bistro' 'American Restaurant'
 'Indonesian Restaurant' 'Buffet' 'Malay Restaurant' 'Pizza Place'
 'BBQ Joint' 'Restaurant' 'Portuguese Restaurant' 'Thai Restaurant'
 'Noodle House' 'Food Truck' 'Comfort Food Restaurant' 'Hainan Restaurant'
 'Fried Chicken Joint' 'Snack Place' 'Breakfast Spot' 'Food'
 'Hong Kong Restaurant' 'Wings Joint' 'Mexican Restaurant'
 'Middle Eastern Restaurant' 'Modern European Restaurant'
 'Shaanxi Restaurant' 'Hakka Restaurant' 'Gastropub'
 'Chinese Br

## Analysing the Eateries and Restaurants Around Each Station

In [16]:
# One hot encoding for the restaurant categories
df_onehot = pd.get_dummies(df_food[['Venue Category']], prefix = '', prefix_sep = '')
# Add column with station names
df_onehot['Station Name'] = df_food['Station Name']
# Move station names column to the first column
fixed_columns = [df_onehot.columns[-1]] + list(df_onehot.columns[:-1])
df_onehot = df_onehot[fixed_columns]

display(df_onehot.head())

Station Name  African Restaurant  American Restaurant  \
0  Jurong East                   0                    0   
1  Jurong East                   0                    0   
2  Jurong East                   0                    0   
3  Jurong East                   0                    0   
4  Jurong East                   0                    0   

   Argentinian Restaurant  Asian Restaurant  Australian Restaurant  \
0                       0                 0                      0   
1                       0                 0                      0   
2                       0                 0                      0   
3                       0                 0                      0   
4                       0                 0                      0   

   Austrian Restaurant  BBQ Joint  Bagel Shop  Bakery  ...  Taco Place  \
0                    0          0           0       0  ...           0   
1                    0          0           0       1  ...           0   
2                    0          0           0       0  ...           0   
3                    0          0           0       0  ...           0   
4                    0          0           0       0  ...           0   

   Taiwanese Restaurant  Tapas Restaurant  Thai Restaurant  Theme Restaurant  \
0                     0                 0                0                 0   
1                     0                 0                0                 0   
2                     0                 0                0                 0   
3                     0                 0                0                 0   
4                     0                 0                0                 0   

   Turkish Restaurant  Vegetarian / Vegan Restaurant  Vietnamese Restaurant  \
0                   0                              0                      0   
1                   0                              0                      0   
2                   0                              0                      0   
3                   0                              0                      0   
4                   0                              1                      0   

   Wings Joint  Yunnan Restaurant  
0            0                  0  
1            0                  0  
2            0                  0  
3            0                  0  
4            0                  0  

[5 rows x 107 columns]

### Group by train station and take mean frequency of occurence of each category

In [17]:
df_food_grouped = df_onehot.groupby('Station Name').mean().reset_index()
display(df_food_grouped)

Station Name  African Restaurant  American Restaurant  \
0       Admiralty            0.000000             0.000000   
1        Aljunied            0.026316             0.000000   
2      Ang Mo Kio            0.000000             0.025641   
3         Bartley            0.000000             0.000000   
4        Bayfront            0.000000             0.000000   
..            ...                 ...                  ...   
117     Woodleigh            0.000000             0.000000   
118       Yew Tee            0.000000             0.000000   
119  Yio Chu Kang            0.000000             0.000000   
120        Yishun            0.000000             0.024390   
121     one-north            0.000000             0.000000   

     Argentinian Restaurant  Asian Restaurant  Australian Restaurant  \
0                       0.0          0.000000                    0.0   
1                       0.0          0.078947                    0.0   
2                       0.0          0.051282                    0.0   
3                       0.0          0.125000                    0.0   
4                       0.0          0.058824                    0.0   
..                      ...               ...                    ...   
117                     0.0          0.200000                    0.0   
118                     0.0          0.000000                    0.0   
119                     0.0          0.058824                    0.0   
120                     0.0          0.000000                    0.0   
121                     0.0          0.022222                    0.0   

     Austrian Restaurant  BBQ Joint  Bagel Shop    Bakery  ...  Taco Place  \
0                    0.0   0.000000         0.0  0.333333  ...         0.0   
1                    0.0   0.026316         0.0  0.000000  ...         0.0   
2                    0.0   0.000000         0.0  0.025641  ...         0.0   
3                    0.0   0.000000         0.0  0.000000  ...         0.0   
4                    0.0   0.000000         0.0  0.000000  ...         0.0   
..                   ...        ...         ...       ...  ...         ...   
117                  0.0   0.200000         0.0  0.200000  ...         0.0   
118                  0.0   0.000000         0.0  0.166667  ...         0.0   
119                  0.0   0.000000         0.0  0.000000  ...         0.0   
120                  0.0   0.000000         0.0  0.048780  ...         0.0   
121                  0.0   0.022222         0.0  0.000000  ...         0.0   

     Taiwanese Restaurant  Tapas Restaurant  Thai Restaurant  \
0                     0.0          0.000000         0.000000   
1                     0.0          0.000000         0.026316   
2                     0.0          0.000000         0.000000   
3                     0.0          0.000000         0.000000   
4                     0.0          0.000000         0.000000   
..                    ...               ...              ...   
117                   0.0          0.000000         0.000000   
118                   0.0          0.000000         0.000000   
119                   0.0          0.000000         0.000000   
120                   0.0          0.000000         0.000000   
121                   0.0          0.022222         0.044444   

     Theme Restaurant  Turkish Restaurant  Vegetarian / Vegan Restaurant  \
0            0.000000                 0.0                       0.000000   
1            0.000000                 0.0                       0.078947   
2            0.000000                 0.0                       0.025641   
3            0.000000                 0.0                       0.000000   
4            0.029412                 0.0                       0.000000   
..                ...                 ...                            ...   
117          0.000000                 0.0                       0.000000   
118          0.000000                 0.0                       0.000000   
119  

### Convert to dataframe of top 10 venues for each train station

In [18]:
# Function to sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Station Name']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
df_food_sorted = pd.DataFrame(columns=columns)
df_food_sorted['Station Name'] = df_food_grouped['Station Name']

for ind in np.arange(df_food_grouped.shape[0]):
    df_food_sorted.iloc[ind, 1:] = return_most_common_venues(df_food_grouped.iloc[ind, :], num_top_venues)

display(df_food_sorted.head())

Station Name 1st Most Common Venue 2nd Most Common Venue  \
0    Admiralty                Bakery            Food Court   
1     Aljunied          Noodle House    Chinese Restaurant   
2   Ang Mo Kio            Food Court  Fast Food Restaurant   
3      Bartley          Noodle House     Indian Restaurant   
4     Bayfront                  Café                Bistro   

           3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Burger Joint    Seafood Restaurant          Noodle House   
1  Vegetarian / Vegan Restaurant      Asian Restaurant            Food Court   
2            Japanese Restaurant      Sushi Restaurant    Chinese Restaurant   
3               Asian Restaurant    Seafood Restaurant     Korean Restaurant   
4            Japanese Restaurant    Italian Restaurant    Chinese Restaurant   

  6th Most Common Venue 7th Most Common Venue  \
0           Snack Place     Fish & Chips Shop   
1                  Café        Breakfast Spot   
2      Asian Restaurant        Sandwich Place   
3            Food Truck                  Café   
4          Noodle House      Asian Restaurant   

             8th Most Common Venue 9th Most Common Venue  \
0                            Diner    Dongbei Restaurant   
1               Dim Sum Restaurant    Seafood Restaurant   
2                      Snack Place        Breakfast Spot   
3                Yunnan Restaurant     Fish & Chips Shop   
4  Southern / Soul Food Restaurant   Dumpling Restaurant   

  10th Most Common Venue  
0             Donut Shop  
1      Indian Restaurant  
2           Burger Joint  
3     Dongbei Restaurant  
4   Cantonese Restaurant

## Cluster Train Stations

In [19]:
kclusters = 10 # number of clusters
df_food_cluster = df_food_grouped.drop('Station Name', 1)

kmeans = KMeans(n_clusters = kclusters, random_state = 0).fit(df_food_cluster)
df_food_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

df_food_final = df_food
df_food_final = df_food_final.join(df_food_sorted.set_index('Station Name'), on = 'Station Name')

df_food_final.head()

Station Name  Station Latitude  Station Longitude  \
0  Jurong East          1.332155         103.742984   
1  Jurong East          1.332155         103.742984   
2  Jurong East          1.332155         103.742984   
3  Jurong East          1.332155         103.742984   
4  Jurong East          1.332155         103.742984   

                                               Venue  Venue Latitude  \
0                          Song Fa Bak Kut Teh 松發肉骨茶        1.333394   
1                                        Johan Paris        1.334083   
2  Tonkatsu by Ma Maison とんかつ マメゾン (Tonkatsu by M...        1.333668   
3                    Dian Xiao Er 店小二 (Dian Xiao Er)        1.333447   
4                                          Green Dot        1.333641   

   Venue Longitude                 Venue Category  Cluster Labels  \
0       103.743420             Chinese Restaurant               2   
1       103.742384                         Bakery               2   
2       103.742818            Japanese Restaurant               2   
3       103.743094             Chinese Restaurant               2   
4       103.742858  Vegetarian / Vegan Restaurant               2   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                  Café   Japanese Restaurant    Chinese Restaurant   
1                  Café   Japanese Restaurant    Chinese Restaurant   
2                  Café   Japanese Restaurant    Chinese Restaurant   
3                  Café   Japanese Restaurant    Chinese Restaurant   
4                  Café   Japanese Restaurant    Chinese Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Food Court  Fast Food Restaurant        Sandwich Place   
1            Food Court  Fast Food Restaurant        Sandwich Place   
2            Food Court  Fast Food Restaurant        Sandwich Place   
3            Food Court  Fast Food Restaurant        Sandwich Place   
4            Food Court  Fast Food Restaurant        Sandwich Place   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0     Korean Restaurant                Bakery            Steakhouse   
1     Korean Restaurant                Bakery            Steakhouse   
2     Korean Restaurant                Bakery            Steakhouse   
3     Korean Restaurant                Bakery            Steakhouse   
4     Korean Restaurant                Bakery            Steakhouse   

  10th Most Common Venue  
0       Asian Restaurant  
1       Asian Restaurant  
2       Asian Restaurant  
3       Asian Restaurant  
4       Asian Restaurant

### Create Map

In [20]:
# initialise map
sg_lat, sg_lng = 1.3521, 103.8198
map_main = folium.Map(location=[sg_lat, sg_lng], zoom_start = 11)

x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers
markers_colors = []
for lat, lng, stn, cluster in zip(df_food_final['Station Latitude'],
                                  df_food_final['Station Longitude'],
                                  df_food_final['Station Name'],
                                  df_food_final['Cluster Labels']):
    label = folium.Popup(str(stn) + ' Cluster ' + str(cluster), parse_html = True)
    folium.CircleMarker([lat, lng],
                        radius = 5,
                        popup = label,
                        color = rainbow[cluster-1],
                        fill = True,
                        fill_color = rainbow[cluster-1],
                        fill_opacity = 0.7).add_to(map_main)

map_main

### New Function to Map a Certain Type of Restaurant

In [21]:
# df <- station list
# df_food <- food venue list
df.head()

StationCode    StationName  Opening  Latitude   Longitude
0    NS1 EW24    Jurong East     1990  1.332155  103.742984
1         NS2    Bukit Batok     1990  1.349057  103.749591
2         NS3   Bukit Gombak     1990  1.358812  103.751501
3     NS4 BP1  Choa Chu Kang     1990  1.384298  103.743855
4         NS5        Yew Tee     1996  1.397149  103.747527

In [22]:
def MapFood(venuetype = None, cluster = False):
    # filter
    if venuetype in venuetype_list:
        df_filtered = df_food.loc[df_food['Venue Category'] == venuetype]
    else:
        df_filtered = df_food

    # create map
    # initialise map
    sg_lat, sg_lng = 1.3521, 103.8198
    map_main = folium.Map(location=[sg_lat, sg_lng], zoom_start = 11)

    # add MRT stations
    for code, station, lat, lng in zip(df['StationCode'], 
                                       df['StationName'], 
                                       df['Latitude'], 
                                       df['Longitude']):
        label = folium.Popup('{} {}'.format(code, station), parse_html = True)
        folium.CircleMarker(
            location = [lat, lng],
            radius = 3,
            color = 'red',
            popup = label,
            fill = True,
            fill_color = 'red'
        ).add_to(map_main)

    # add restaurants
    if cluster:
        mc = MarkerCluster()

        for venue, lat, lng in zip(df_filtered['Venue'], 
                                   df_filtered['Venue Latitude'], 
                                   df_filtered['Venue Longitude']):
            label = folium.Popup(venue, parse_html = True)
            mc.add_child(folium.Marker(
                location = [lat, lng],
                radius = 2,
                popup = label,
                color = 'blue',
                fill = True,
                fill_color = '#3186cc',
                fill_opacity = 0.7,
                parse_html = False,
                icon = folium.Icon(icon = 'cutlery')
            ))

        map_main.add_child(mc)

    else:
        for venue, lat, lng in zip(df_filtered['Venue'], 
                                   df_filtered['Venue Latitude'], 
                                   df_filtered['Venue Longitude']):
            label = folium.Popup(venue, parse_html = True)
            folium.CircleMarker(
                location = [lat, lng],
                radius = 2,
                popup = label,
                color = 'blue',
                fill = True,
                fill_color = '#3186cc',
                fill_opacity = 0.7,
                parse_html = False
            ).add_to(map_main)
    
    display(map_main)

In [23]:
MapFood('Indian Restaurant', False)

In [24]:
MapFood('Indian Restaurant', True)

In [25]:
MapFood('Mexican Restaurant', False)

In [26]:
MapFood('Mexican Restaurant', True)